In [1]:
import pandas as pd
from pandas import DataFrame as df
import re
from tqdm import tqdm
from nltk.tokenize import word_tokenize
import os
from konlpy.tag import Okt
okt=Okt()
from sklearn.feature_extraction.text import TfidfVectorizer 
import operator

pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)



pd.set_option('display.max_colwidth',-1)
job=pd.read_csv('workspace_210202073425765gyjf_210329052850JgqyH4a_210329052850jx3dMNE.csv')
major=pd.read_csv('workspace_210202073425765gyjf_210329052850KBm53GD_210329052850VYbN6AO.csv')

<ipython-input-1-c231fedca7c2>:17: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('display.max_colwidth',-1)


## 문서 당 개수

In [2]:
print('직업개수 : ',len(job))
print('학과개수 : ',len(major))

직업개수 :  120
학과개수 :  289


## 각 문서 예시

In [3]:
print('직업 예시\n')
print(job.loc[0], '\n\n\n')
print('학과 예시\n')
print(major.loc[0])

직업 예시

id                       44                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

## 각 함수들

In [4]:
survive = re.compile('[^ a-zA-Z()[]ㄱ-ㅣ가-힣]+')
english = re.compile('[^a-zA-Z]+')
hangul = re.compile('[^ ㄱ-ㅣ가-힣]')
hangul_ = re.compile('[^ ㄱ-ㅣ가-힣,]')


# 오류 문자들 제거
def clean(document,sub):
    result=[]
    for i in range(len(document)):
        answer = list(document[sub])[i]
        text = answer.replace('<h1>','').replace('&middot;','').replace('</h1>',' ').replace('\r','').replace('\n','').replace('<p>','').replace('&nbsp;',' ').replace('</p>','').replace('&lsquo;','').replace('&rsquo;','').replace('<br />','')
        result.append(text)    
    return result


# 오류문자 제거 후, 명사들만 남기기
def make_nouns(document,sub):
    result=[]
    for i in range(len(document)):
        answer = list(document[sub])[i]
        text = answer.replace('<h1>','').replace('&middot;','').replace('</h1>',' ').replace('\r','').replace('\n','').replace('<p>','').replace('&nbsp;',' ').replace('</p>','').replace('&lsquo;','').replace('&rsquo;','').replace('<br />','')
        kor = ' '.join(okt.nouns(text)).split()
        eng = english.sub(' ', text).split()
        index_eng = 0
        index_kor = 0
        ans=[]        
        if len(eng) == 0:
            result.append(' '.join(kor).replace(' 란 ',' ').replace(' 등 ',' '))
        else:
            while True:
                a = kor[index_kor]
                b = eng[index_eng]
                if answer.find(a) < answer.find(b):
                    ans.append(a)
                    answer = answer[answer.find(a)+len(a):]
                    index_kor += 1
                else:
                    ans.append(b)
                    answer = answer[answer.find(b)+len(b):]
                    index_eng += 1
                if index_eng == len(eng) or index_kor == len(kor):
                    if index_kor != len(kor):
                        while index_kor != len(kor):
                            ans.append(kor[index_kor])
                            index_kor += 1
                    else:
                        while index_eng != len(eng):
                            ans.append(eng[index_eng])
                            index_eng +=1
                    break
            result.append(' '.join(ans).replace(' 란 ',' ').replace(' 등 ',' '))
    return (result)


# aptitude 정리
def preprocessing_apptitude(the_list):
    while '' in the_list:
        the_list.remove('')
    for i in range(len(the_list)):
        the_list[i] = the_list[i].lstrip().rstrip()
    return the_list


#양쪽 공백 제거
def remove_blank(the_list):
    for i in range(len(the_list)):
        the_list[i] = the_list[i].lstrip().rstrip()
    return the_list



# 과목 정리 / 과목별로 앞에 분야 기입
def subject(the_list):
    flag = 0
    for i in range(len(the_list)):    
        if '진로 ' in the_list[i]:
            flag = 1
        if '필수 ' in the_list[i]:
            flag = 2
        if flag == 0 and '일반 ' not in the_list[i]:
            the_list[i] = '[일반] '+the_list[i]
        elif flag == 0 and '일반 ' in the_list[i]:
            the_list[i]=the_list[i].replace('일반','[일반]')
        elif flag == 1 and '진로 ' not in the_list[i]:
            the_list[i] = '[진로] '+the_list[i]
        elif flag == 1 and '진로 ' in the_list[i]:
            the_list[i] = the_list[i].replace('진로','[진로]')
        elif flag == 2 and '필수 ' not in the_list[i]:
            the_list[i] = '[필수] '+the_list[i]
        else:
            the_list[i]=the_list[i].replace('필수','[필수]')

    return the_list

## 정리된, 새로운 DF 구성

###  cleaned_job, clean_major은 정리된거
### new_job, new_major는 정리된거 + 명사화까지 적용

In [5]:
temp0 = []
temp1 = []
temp2=clean(job,'content')
temp3 = []
temp4 = []
temp5 = []
temp6 = []
temp7 = []

for i in range(len(job)):
    temp0.append(job['name'][i])
    temp1.append(job['primary_major'][i])
    temp3.append(preprocessing_apptitude(hangul.sub('',job['aptitudes'][i]).split('  ')))
    temp4.append(remove_blank(hangul_.sub('',job['personality_types'][i]).split(',')))
    temp5.append(remove_blank(hangul_.sub('',job['related_jobs'][i]).split(',')))
    temp6.append(hangul.sub('',job['related_majors'][i]).split()[1::2])
    temp7.append(remove_blank(hangul_.sub('',job['related_subjects'][i]).split(',')))
    
cleaned_job = pd.DataFrame({'직업':temp0,'학과':temp1,'내용':temp2,'적성':temp3,'성격타입':temp4,'관련직업':temp5,'관련학과':temp6,'관련과목':temp7})    
    

    
    
    
    
    
temp_0 = []
temp_1 = clean(major,'content')
temp_2 = clean(major,'tips')
temp_3 = []
temp_4 = []
temp_5 = clean(major,'aptitudes')
temp_6 = []

for i in range(len(major)):
    temp_0.append(major['title'][i])
    temp_3.append(major['books'][i])
    temp_4.append(subject(remove_blank(hangul_.sub('',major['subjects'][i]).split(','))))
    temp_6.append(major['family'][i])
    
cleaned_major = pd.DataFrame({'학과':temp_0,'내용':temp_1,'팁':temp_2,'책':temp_3,'과목':temp_4,'적성':temp_5,'계열':temp_6})    
 

In [6]:
temp0 = []
temp1 = []
temp2=make_nouns(job,'content')
temp3 = []
temp4 = []
temp5 = []
temp6 = []
temp7 = []

for i in range(len(job)):
    temp0.append(job['name'][i])
    temp1.append(job['primary_major'][i])
    temp3.append(preprocessing_apptitude(hangul.sub('',job['aptitudes'][i]).split('  ')))
    temp4.append(remove_blank(hangul_.sub('',job['personality_types'][i]).split(',')))
    temp5.append(remove_blank(hangul_.sub('',job['related_jobs'][i]).split(',')))
    temp6.append(hangul.sub('',job['related_majors'][i]).split()[1::2])
    temp7.append(remove_blank(hangul_.sub('',job['related_subjects'][i]).split(',')))
    
new_job = pd.DataFrame({'직업':temp0,'학과':temp1,'내용':temp2,'적성':temp3,'성격타입':temp4,'관련직업':temp5,'관련학과':temp6,'관련과목':temp7})    
    

    
    
    
    
    
temp_0 = []
temp_1 = make_nouns(major,'content')
temp_2 = make_nouns(major,'tips')
temp_3 = []
   
temp_4 = []
temp_5 = make_nouns(major,'aptitudes')
temp_6 = []

for i in range(len(major)):
    temp_0.append(major['title'][i])
    temp_3.append(major['books'][i])
    temp_4.append(subject(remove_blank(hangul_.sub('',major['subjects'][i]).split(','))))
    temp_6.append(major['family'][i])
    
new_major = pd.DataFrame({'학과':temp_0,'내용':temp_1,'팁':temp_2,'책':temp_3,'과목':temp_4,'적성':temp_5,'계열':temp_6})    
 

## 직업데이터의 '연관 학과'에 학과데이터가 포함되었는지 확인

### 289개 중 164개는 포함됨, 나머지 125개 학과는 직접 보고 변경

### 직업데이터 속 '연관 학과'에 직접 추가해줘서 포함시키고 너무 연관되는 학과가 없는 경우 삭제..ㅠ

In [7]:
temp=[]
for i in range(len(list(new_job['관련학과']))):
    temp.extend(list(new_job['관련학과'])[i])
    temp.append(new_job['학과'][i])



a=0
b=0
for i in range(len(new_major)):
    if new_major['학과'][i] in temp:
        print(new_major['학과'][i], '있음!!!!!!!!!!!!')
        a+=1
    else:
        print(new_major['학과'][i],'없음ㅠㅠ')
        b+=1
        
print(a,b)

경영정보학과 없음ㅠㅠ
노어노문학과 없음ㅠㅠ
동양어문학과 없음ㅠㅠ
문예창작학과 있음!!!!!!!!!!!!
문헌정보학과 있음!!!!!!!!!!!!
(고고)문화인류학과 없음ㅠㅠ
문화재학과 없음ㅠㅠ
북한학과 없음ㅠㅠ
불어불문학과 없음ㅠㅠ
사학과 있음!!!!!!!!!!!!
관현악과 있음!!!!!!!!!!!!
스페인어학과 없음ㅠㅠ
심리학과 있음!!!!!!!!!!!!
언어학과 있음!!!!!!!!!!!!
영어통번역학부 없음ㅠㅠ
일어일문학과 없음ㅠㅠ
국제학부 없음ㅠㅠ
자율전공학부 없음ㅠㅠ
경영학과 있음!!!!!!!!!!!!
공공행정학과 없음ㅠㅠ
관광경영학과 있음!!!!!!!!!!!!
공공인재학과 없음ㅠㅠ
글로벌경영학과 없음ㅠㅠ
관광학과 없음ㅠㅠ
광고홍보학과 있음!!!!!!!!!!!!
국제관계학과 있음!!!!!!!!!!!!
군사학과 있음!!!!!!!!!!!!
금융보험학과 있음!!!!!!!!!!!!
기술경영학과 없음ㅠㅠ
농업경제학과 없음ㅠㅠ
도시계획부동산학과 있음!!!!!!!!!!!!
도시행정학과 없음ㅠㅠ
무역학과 있음!!!!!!!!!!!!
미디어학부 없음ㅠㅠ
수학교육과 있음!!!!!!!!!!!!
아동복지학과 있음!!!!!!!!!!!!
부동산학과 없음ㅠㅠ
사회복지학과 있음!!!!!!!!!!!!
세무회계학과 있음!!!!!!!!!!!!
언론정보학과 없음ㅠㅠ
식품자원경제학과 없음ㅠㅠ
신문방송학과 있음!!!!!!!!!!!!
아동-청소년학과 없음ㅠㅠ
응용통계학과 없음ㅠㅠ
의료경영학과 있음!!!!!!!!!!!!
치위생학과 있음!!!!!!!!!!!!
정치외교학과 있음!!!!!!!!!!!!
지리학과 있음!!!!!!!!!!!!
행정학과 있음!!!!!!!!!!!!
항공서비스학과 있음!!!!!!!!!!!!
호텔경영학과 있음!!!!!!!!!!!!
과학교육과 있음!!!!!!!!!!!!
교육공학과 없음ㅠㅠ
방사선학과 있음!!!!!!!!!!!!
국어교육과 있음!!!!!!!!!!!!
물리교육과 있음!!!!!!!!!!!!
미술교육과 있음!!!!!!!!!!!!
영어교육과 없음ㅠㅠ
생물교육과 있음!!!!!!!!!

In [8]:
# 관련 학과에 학과 추가하기
def arrange(major,add_major):
    temp = list(cleaned_job.loc[cleaned_job.index[cleaned_job['학과'] == major]]['관련학과'])
    temp[0].append(add_major)
    cleaned_job.loc[cleaned_job.index[cleaned_job['학과'] == major],'관련학과'] = temp
    new_job.loc[cleaned_job.index[cleaned_job['학과'] == major],'관련학과'] = temp

In [9]:
arrange('통계학과','경영정보학과')

arrange('영어학과','노어노문학과')
arrange('국어(영어 및 기타 외국어)교육학과','노어노문학과')

arrange('언어학과','동양어문학과')
arrange('국어(영어 및 기타 외국어)교육학과','동양어문학과')

arrange('역사학과','(고고)문화인류학과')
arrange('문헌정보학과','(고고)문화인류학과')

arrange('역사학과','문화재학과')
arrange('문헌정보학과','문화재학과')

arrange('정치외교학과','북한학과')

arrange('영어학과','불어불문학과')
arrange('국어(영어 및 기타 외국어)교육학과','불어불문학과')

arrange('영어학과','스페인어학과')
arrange('국어(영어 및 기타 외국어)교육학과','스페인어학과')

arrange('영어학과','영어통번역학부')
arrange('국어(영어 및 기타 외국어)교육학과','영어통번역학부')

arrange('영어학과','일어일문학과')
arrange('국어(영어 및 기타 외국어)교육학과','일어일문학과')

arrange('사회학과','국제학부')
arrange('정치외교학과','국제학부')
arrange('사회학과','국제학부')

arrange('국제관계학과','자율전공학부')
arrange('경영학과','자율전공학부')

arrange('행정학과','공공행정학과')
arrange('보건행정학과','공공행정학과')
arrange('동물자원학과','공공행정학과')
arrange('사회복지학과','공공행정학과')
arrange('경찰행정학과','공공행정학과')
arrange('도시공학과','공공행정학과')

arrange('사회학과','공공인재학과')

arrange('경영학과','글로벌경영학과')
arrange('무역학과','글로벌경영학과')
arrange('회계학과','글로벌경영학과')
arrange('국제관계학과','글로벌경영학과')
arrange('사회학과','글로벌경영학과')

arrange('영어학과','관광학과')
arrange('관광경영학과','관광학과')
arrange('국제관계학과','관광학과')

arrange('통계학과','기술경영학과')

arrange('식물자원학과','농업경제학과')
arrange('토목공학과','농업경제학과')
arrange('생물학과','농업경제학과')
arrange('공학교육학과','농업경제학과')

arrange('토목공학과','도시행정학과')
arrange('도시계획학과','도시행정학과')
arrange('도시공학과','도시행정학과')

arrange('미술학과','미디어학부')
arrange('신문방송학과','미디어학부')

arrange('법학과','부동산학과')
arrange('도시공학과','부동산학과')
arrange('도시계획학과','부동산학과')

arrange('신문방송학과','언론정보학과')
arrange('정치외교학과','언론정보학과')
arrange('문예창작학과','언론정보학과')

arrange('보건학과','식품자원경제학과')
arrange('식품가공학과','식품자원경제학과')
arrange('식품영양학과','식품자원경제학과')

arrange('교육학과','아동-청소년학과')
arrange('아동학과','아동-청소년학과')
arrange('사회복지학과','아동-청소년학과')

arrange('통계학과','응용통계학과')
arrange('응용소프트웨어공학과','응용통계학과')
arrange('금융보험학과','응용통계학과')
arrange('수학과','응용통계학과')

arrange('수학교육학과','교육공학과')
arrange('과학교육학과','교육공학과')
arrange('초등교육학과','교육공학과')
arrange('공학교육학과','교육공학과')
arrange('아동학과','교육공학과')
arrange('유아교육학과','교육공학과')
arrange('교육학과','교육공학과')

arrange('교육학과','영어교육과')
arrange('초등교육학과','영어교육과')
arrange('국어(영어 및 기타 외국어)교육학과','영어교육과')


arrange('생명과학과','임산생명공학과')

arrange('사회(지리, 역사, 윤리)교육학과','역사교육과')

arrange('사회(지리, 역사, 윤리)교육학과','윤리교육과')

arrange('사회(지리, 역사, 윤리)교육학과','일반사회교육과')

arrange('국어(영어 및 기타 외국어)교육학과','일어교육과')

arrange('사회(지리, 역사, 윤리)교육학과','지리교육과')

arrange('사회(지리, 역사, 윤리)교육학과','한문교육과')

arrange('화학과','공업화학과')
arrange('에너지공학과','공업화학과')

arrange('유아교육학과','가정아동복지학과')

arrange('생물학과','농생물학과')
arrange('공학교육학과','농생물학과')
arrange('식물자원학과','농생물학과')
arrange('생명과학과','농생물학과')

arrange('공학교육학과','멀티미디어학과')
arrange('정보통신공학과','멀티미디어학과')
arrange('미술학과','멀티미디어학과')

arrange('생물학과','미래농업융합학부')
arrange('식물자원학과','미래농업융합학부')
arrange('생명과학과','미래농업융합학부')

arrange('생물학과','미생물분자생명과학과')
arrange('식물자원학과','미생물분자생명과학과')
arrange('생명과학과','미생물분자생명과학과')

arrange('공학교육학과','모바일공학과')
arrange('응용소프트웨어공학과','모바일공학과')
arrange('반도체공학과','모바일공학과')
arrange('의료공학과','모바일공학과')

arrange('원예학과','산림학과')

arrange('원예학과','산림환경시스템학과')
arrange('대기과학과','산림환경시스템학과')

arrange('생명과학과','생물환경화학과')
arrange('생물학과','생물환경화학과')
arrange('화학과','생물환경화학과')

arrange('지질학과','건설시스템공학과')
arrange('공학교육학과','건설시스템공학과')
arrange('토목공학과','건설시스템공학과')
arrange('건축공학과','건설시스템공학과')
arrange('도시공학과','건설시스템공학과')

arrange('통계학과','정보통계학과')
arrange('응용소프트웨어공학과','정보통계학과')
arrange('금융보험학과','정보통계학과')
arrange('소프트웨어공학과','정보통계학과')
arrange('응용소프트웨어공학과','정보통계학과')
arrange('반도체공학과','정보통계학과')
arrange('컴퓨터공학과','정보통계학과')


arrange('호텔경영학과','외식산업학과')
arrange('식품조리학과','외식산업학과')
arrange('식품영양학과','외식산업학과')

arrange('체육교육학과','스포츠산업학과')
arrange('체육학과','스포츠산업학과')
arrange('사회체육학과','스포츠산업학과')


arrange('소프트웨어공학과','공간정보공학과')
arrange('지질학과','공간정보공학과')
arrange('도시공학과','공간정보공학과')
arrange('도시계획학과','공간정보공학과')

arrange('과학교육학과','생물공학과')
arrange('수산학과','생물공학과')
arrange('생명과학과','생물공학과')
arrange('생물학과','생물공학과')

arrange('항공우주공학과','드론교통공학과')
arrange('제어로봇공학과','드론교통공학과')
arrange('교통공학과','드론교통공학과')
arrange('제어로봇공학과','드론교통공학과')


arrange('만화애니메이션학과','디지털콘텐츠학과')
arrange('신문방송학과','디지털콘텐츠학과')
arrange('공학교육학과','디지털콘텐츠학과')
arrange('사진학과','디지털콘텐츠학과')
arrange('미술학과','디지털콘텐츠학과')
arrange('철학과','디지털콘텐츠학과')

arrange('공학교육학과','멀티미디어공학과')
arrange('정보통신공학과','멀티미디어공학과')
arrange('미술학과','멀티미디어공학과')
arrange('신문방송학과','멀티미디어공학과')


arrange('반도체공학과','반도체시스템공학과')
arrange('전자공학과','반도체시스템공학과')
arrange('신소재공학과','반도체시스템공학과')
arrange('공학교육학과','반도체시스템공학과')
arrange('전기공학과','반도체시스템공학과')

arrange('소프트웨어공학과','산업경영공학과')
arrange('통계학과','산업경영공학과')
arrange('대기과학과','산업경영공학과')
arrange('도시계획학과','산업경영공학과')
arrange('환경학과','산업경영공학과')
arrange('도시공학과','산업경영공학과')
arrange('무역학과','산업경영공학과')
arrange('경영학과','산업경영공학과')

arrange('통계학과','산업시스템공학과')
arrange('대기과학과','산업시스템공학과')
arrange('도시계획학과','산업시스템공학과')
arrange('환경학과','산업시스템공학과')
arrange('무역학과','산업시스템공학과')

arrange('소프트웨어공학과','소프트웨어융합공학과')
arrange('통계학과','소프트웨어융합공학과')
arrange('응용소프트웨어공학과','소프트웨어융합공학과')
arrange('반도체공학과','소프트웨어융합공학과')
arrange('제어로봇공학과','소프트웨어융합공학과')
arrange('컴퓨터공학과','소프트웨어융합공학과')
arrange('정보통신공학과','소프트웨어융합공학과')
arrange('의료공학과','소프트웨어융합공학과')

arrange('공학교육학과','자동차IT융합학과')
arrange('전기공학과','자동차IT융합학과')
arrange('반도체공학과','자동차IT융합학과')
arrange('제어로봇공학과','자동차IT융합학과')
arrange('기계공학과','자동차IT융합학과')
arrange('자동차공학과','자동차IT융합학과')


arrange('통계학과','정보보안학과')
arrange('응용소프트웨어공학과','정보보안학과')
arrange('반도체공학과','정보보안학과')
arrange('컴퓨터공학과','정보보안학과')
arrange('소프트웨어공학과','정보보안학과')
arrange('경제학과','정보보안학과')
arrange('정보통신공학과','정보보안학과')


arrange('수산학과','조선해양시스템공학과')
arrange('해양공학과','조선해양시스템공학과')
arrange('기계공학과','조선해양시스템공학과')

arrange('지질학과','지역건설공학과')
arrange('공학교육학과','지역건설공학과')
arrange('토목공학과','지역건설공학과')
arrange('행정학과','지역건설공학과')
arrange('건축공학과','지역건설공학과')
arrange('도시공학과','지역건설공학과')

arrange('해양공학과','항해학부')

arrange('화학과','화장품공학과')
arrange('미용과','화장품공학과')

arrange('보건학과','안경광학과')

arrange('연극영화학과','모델과')

arrange('무용학과','뮤지컬학과')
arrange('성악과','뮤지컬학과')
arrange('작곡과','뮤지컬학과')
arrange('공연예술학과','뮤지컬학과')
arrange('연극영화학과','뮤지컬학과')
arrange('대중음악과','뮤지컬학과')
arrange('철학과','뮤지컬학과')

arrange('공학교육학과','뷰티_미용_산업_예술학과')
arrange('미용과','뷰티_미용_산업_예술학과')


arrange('역사학과','서양화과')

arrange('체육교육학과','스포츠의학과_예체능')
arrange('체육학과','스포츠의학과_예체능')
arrange('물리치료학과','스포츠의학과_예체능')
arrange('작업치료학과','스포츠의학과_예체능')

arrange('영상예술학과','영상디자인학과')
arrange('광고홍보학과','영상디자인학과')
arrange('시각디자인학과','영상디자인학과')
arrange('문예창작학과','영상디자인학과')
arrange('만화애니메이션학과','영상디자인학과')
arrange('신문방송학과','영상디자인학과')


arrange('소프트웨어공학과','환경디자인과')
arrange('시각디자인학과','환경디자인과')
arrange('도시공학과','환경디자인과')
arrange('도시계획학과','환경디자인과')
arrange('산업디자인학과','환경디자인과')

arrange('예술치료학과','조소과')
arrange('음악(미술)교육학과','조소과')
arrange('만화애니메이션학과','조소과')


arrange('무역학과','소비자학과')
arrange('광고홍보학과','소비자학과')
arrange('경제학과','소비자학과')
arrange('회계학과','소비자학과')
arrange('세무학과','소비자학과')

arrange('사회(지리, 역사, 윤리)교육학과','고고학과')
arrange('언어학과','고고학과')
arrange('역사학과','고고학과')

arrange('영어학과','독어독문학과')
arrange('국어(영어 및 기타 외국어)교육학과','독어독문학과')

arrange('영상예술학과','문화콘텐츠학과')
arrange('공연예술학과','문화콘텐츠학과')
arrange('신문방송학과','문화콘텐츠학과')
arrange('연극영화학과','문화콘텐츠학과')
arrange('만화애니메이션학과','문화콘텐츠학과')
arrange('문예창작학과','문화콘텐츠학과')
arrange('광고홍보학과','문화콘텐츠학과')
arrange('철학과','문화콘텐츠학과')


arrange('음악(미술)교육학과','미학과')
arrange('철학과','미학과')
arrange('음악(미술)교육학과','미학과')
arrange('만화애니메이션학과','미학과')
arrange('미술학과','미학과')
arrange('영상예술학과','미학과')


arrange('종교학과','상담심리학과')
arrange('교육학과','상담심리학과')
arrange('초등교육학과','상담심리학과')
arrange('아동학과','상담심리학과')
arrange('사회복지학과','상담심리학과')
arrange('사회학과','상담심리학과')
arrange('특수교육학과','상담심리학과')
arrange('심리학과','상담심리학과')
arrange('언어재활학과','상담심리학과')

arrange('영어학과','아랍어과')
arrange('국어(영어 및 기타 외국어)교육학과','아랍어과')

arrange('영어학과','영어영문학과')
arrange('언어학과','영어영문학과')
arrange('국어(영어 및 기타 외국어)교육학과','영어영문학과')

arrange('언어학과','인류학과')
arrange('역사학과','인류학과')

arrange('영어학과','독어교육과')
arrange('국어(영어 및 기타 외국어)교육학과','아랍어과')

arrange('경영학과','국제통상학과')
arrange('정치외교학과','국제통상학과')
arrange('국제관계학과','국제통상학과')

 
arrange('무역학과','국제물류학과')
arrange('국제관계학과','국제물류학과')

arrange('무역학과','국제경영학과')
arrange('회계학과','국제경영학과')
arrange('세무학과','국제경영학과')
arrange('국제관계학과','국제경영학과')
arrange('정치외교학과','국제경영학과')

arrange('공학교육학과','금융학과')
arrange('경제학과','금융학과')
arrange('수학과','금융학과')
arrange('금융보험학과','금융학과')
arrange('회계학과','금융학과')

arrange('무역학과','글로벌비즈니스학과')
arrange('회계학과','글로벌비즈니스학과')
arrange('세무학과','글로벌비즈니스학과')
arrange('국제관계학과','글로벌비즈니스학과')
arrange('정치외교학과','글로벌비즈니스학과')

arrange('교통공학과','공학교육과')
arrange('공학교육학과','공학교육과')
arrange('전기공학과','공학교육과')
arrange('반도체공학과','공학교육과')
arrange('건축공학과','공학교육과')


arrange('유아교육학과','아동가족학과')
arrange('교육학과','아동가족학과')
arrange('아동학과','아동가족학과')
arrange('사회복지학과','아동가족학과')
arrange('재활학과','아동가족학과')

arrange('보건학과','광학공학과')
arrange('사진학과','광학공학과')

arrange('언어재활학과','재활상담학과')
arrange('교육학과','재활상담학과')
arrange('사회복지학과','재활상담학과')
arrange('재활학과','재활상담학과')
arrange('물리치료학과','재활상담학과')
arrange('예술치료학과','재활상담학과')
arrange('보건행정학과','재활상담학과')
arrange('언어재활학과','재활상담학과')

arrange('교통공학과','항공관광학과')
arrange('항공우주공학과','항공관광학과')
arrange('호텔경영학과','항공관광학과')
arrange('관광경영학과','항공관광학과')

arrange('국어(영어 및 기타 외국어)교육학과','불어교육과')
arrange('영어학과','불어교육과')

arrange('교육학과','기술교육과')
arrange('과학교육학과','기술교육과')
arrange('공학교육학과','기술교육과')
arrange('기계공학과','기술교육과')
arrange('제어로봇공학과','기술교육과')

arrange('화학과','생명나노공학과')
arrange('생물학과','생명나노공학과')
arrange('생명과학과','생명나노공학과')

arrange('사회(지리, 역사, 윤리)교육학과','사회교육과')

arrange('아동학과','아동보육과')
arrange('유아교육학과','아동보육과')
arrange('사회복지학과','아동보육과')
arrange('교육학과','아동보육과')

arrange('통계학과','산업보안학과')
arrange('컴퓨터공학과','산업보안학과')
arrange('응용소프트웨어공학과','산업보안학과')
arrange('반도체공학과','산업보안학과')
arrange('소프트웨어공학과','산업보안학과')
arrange('경제학과','산업보안학과')
arrange('정보통신공학과','산업보안학과')

arrange('국어(영어 및 기타 외국어)교육학과','중국어교육과')
arrange('영어학과','중국어교육과')

arrange('교육학과','특수교육과')
arrange('초등교육학과','특수교육과')
arrange('특수교육학과','특수교육과')
arrange('재활학과','특수교육과')
arrange('예술치료학과','특수교육과')

arrange('지구과학과','물리천문학과')
arrange('대기과학과','물리천문학과')
arrange('물리학과','물리천문학과')
arrange('항공우주공학과','물리천문학과')

arrange('수산학과','수산생명의학과')
arrange('해양공학과','수산생명의학과')
arrange('생명과학과','수산생명의학과')

arrange('생물학과','식물의학과')
arrange('생명과학과','식물의학과')
arrange('식물자원학과','식물의학과')

arrange('보건학과','식품조리과학과')
arrange('식품가공학과','식품조리과학과')
arrange('식품조리학과','식품조리과학과')
arrange('식품영양학과','식품조리과학과')

arrange('환경학과','주거환경학과')
arrange('토목공학과','주거환경학과')
arrange('건축공학과','주거환경학과')
arrange('도시공학과','주거환경학과')
arrange('도시계획학과','주거환경학과')

arrange('수의학과','축산학과')
arrange('동물자원학과','축산학과')

arrange('지구과학과','해양환경과학과')
arrange('수산학과','해양환경과학과')
arrange('해양공학과','해양환경과학과')

arrange('지질학과','건설환경공학과')
arrange('토목공학과','건설환경공학과')
arrange('행정학과','건설환경공학과')
arrange('건축공학과','건설환경공학과')
arrange('도시공학과','건설환경공학과')
arrange('도시계획학과','건설환경공학과')

arrange('소프트웨어공학과','소프트웨어융합학과')
arrange('통계학과','소프트웨어융합학과')
arrange('응용소프트웨어공학과','소프트웨어융합학과')
arrange('반도체공학과','소프트웨어융합학과')
arrange('제어로봇공학과','소프트웨어융합학과')
arrange('컴퓨터공학과','소프트웨어융합학과')
arrange('정보통신공학과','소프트웨어융합학과')
arrange('의료공학과','소프트웨어융합학과')

arrange('토목공학과','안전공학과')
arrange('건축공학과','안전공학과')
arrange('자동차공학과','안전공학과')
arrange('응급구조학과','안전공학과')
arrange('소방방재학과','안전공학과')

arrange('원예학과','원예생명공학과')
arrange('식물자원학과','원예생명공학과')
arrange('공학교육학과','원예생명공학과')

arrange('에너지공학과','원자핵공학과')

arrange('응용소프트웨어공학과','임베디드시스템공학과')
arrange('반도체공학과','임베디드시스템공학과')
arrange('소프트웨어공학과','임베디드시스템공학과')
arrange('컴퓨터공학과','임베디드시스템공학과')

arrange('정보통신공학과','전파정보통신공학과')
arrange('전자공학과','전파정보통신공학과')
arrange('항공우주공학과','전파정보통신공학과')
arrange('교통공학과','전파정보통신공학과')
arrange('소프트웨어공학과','전파정보통신공학과')
arrange('응용소프트웨어공학과','전파정보통신공학과')
arrange('반도체공학과','전파정보통신공학과')

arrange('토목공학과','토목환경공학과')
arrange('지질학과','토목환경공학과')
arrange('건축공학과','토목환경공학과')
arrange('도시공학과','토목환경공학과')

arrange('항공우주공학과','항공시스템공학과')
arrange('교통공학과','항공시스템공학과')
arrange('지구과학과','항공시스템공학과')
arrange('기계공학과','항공시스템공학과')

arrange('항공우주공학과','항공운항학과')

arrange('항공우주공학과','항공정비학과')
arrange('기계공학과','항공정비학과')

arrange('생물학과','화공생명공학과')
arrange('생명과학과','화공생명공학과')
arrange('환경학과','화공생명공학과')

arrange('문예창작학과','방송연예과_전공')
arrange('정치외교학과','방송연예과_전공')
arrange('영상예술학과','방송연예과_전공')
arrange('연극영화학과','방송연예과_전공')
arrange('신문방송학과','방송연예과_전공')

arrange('체육교육학과','스포츠건강관리학과')
arrange('체육학과','스포츠건강관리학과')
arrange('사회체육학과','스포츠건강관리학과')
arrange('작업치료학과','스포츠건강관리학과')
arrange('사회복지학과','스포츠건강관리학과')
arrange('재활학과','스포츠건강관리학과')
arrange('언어재활학과','스포츠건강관리학과')

arrange('시각디자인학과','실내디자인학과')
arrange('미술학과','실내디자인학과')
arrange('영상예술학과','실내디자인학과')
arrange('광고홍보학과','실내디자인학과')
arrange('도시공학과','실내디자인학과')
arrange('산업디자인학과','실내디자인학과')

arrange('음악(미술)교육학과','조형예술학과')
arrange('공예학과','조형예술학과')
arrange('미술학과','조형예술학과')

arrange('공학교육학과','피부미용화장품과학과')
arrange('미용과','피부미용화장품과학과')

arrange('사진학과','사진_영상_예술학과')
arrange('영상예술학과','사진_영상_예술학과')
arrange('미술학과','사진_영상_예술학과')

In [10]:
temp=[]
for i in range(len(list(new_job['관련학과']))):
    temp.extend(list(new_job['관련학과'])[i])
    temp.append(new_job['학과'][i])



a=0
b=0
for i in range(len(new_major)):
    if new_major['학과'][i] in temp:
        print(new_major['학과'][i], '있음!!!!!!!!!!!!')
        a+=1
    else:
        print(new_major['학과'][i],'없음ㅠㅠ')
        b+=1
        
print(a,b)

경영정보학과 있음!!!!!!!!!!!!
노어노문학과 있음!!!!!!!!!!!!
동양어문학과 있음!!!!!!!!!!!!
문예창작학과 있음!!!!!!!!!!!!
문헌정보학과 있음!!!!!!!!!!!!
(고고)문화인류학과 있음!!!!!!!!!!!!
문화재학과 있음!!!!!!!!!!!!
북한학과 있음!!!!!!!!!!!!
불어불문학과 있음!!!!!!!!!!!!
사학과 있음!!!!!!!!!!!!
관현악과 있음!!!!!!!!!!!!
스페인어학과 있음!!!!!!!!!!!!
심리학과 있음!!!!!!!!!!!!
언어학과 있음!!!!!!!!!!!!
영어통번역학부 있음!!!!!!!!!!!!
일어일문학과 있음!!!!!!!!!!!!
국제학부 있음!!!!!!!!!!!!
자율전공학부 있음!!!!!!!!!!!!
경영학과 있음!!!!!!!!!!!!
공공행정학과 있음!!!!!!!!!!!!
관광경영학과 있음!!!!!!!!!!!!
공공인재학과 있음!!!!!!!!!!!!
글로벌경영학과 있음!!!!!!!!!!!!
관광학과 있음!!!!!!!!!!!!
광고홍보학과 있음!!!!!!!!!!!!
국제관계학과 있음!!!!!!!!!!!!
군사학과 있음!!!!!!!!!!!!
금융보험학과 있음!!!!!!!!!!!!
기술경영학과 있음!!!!!!!!!!!!
농업경제학과 있음!!!!!!!!!!!!
도시계획부동산학과 있음!!!!!!!!!!!!
도시행정학과 있음!!!!!!!!!!!!
무역학과 있음!!!!!!!!!!!!
미디어학부 있음!!!!!!!!!!!!
수학교육과 있음!!!!!!!!!!!!
아동복지학과 있음!!!!!!!!!!!!
부동산학과 있음!!!!!!!!!!!!
사회복지학과 있음!!!!!!!!!!!!
세무회계학과 있음!!!!!!!!!!!!
언론정보학과 있음!!!!!!!!!!!!
식품자원경제학과 있음!!!!!!!!!!!!
신문방송학과 있음!!!!!!!!!!!!
아동-청소년학과 있음!!!!!!!!!!!!
응용통계학과 있음!!!!!!!!!!!!
의료경영학과 있음!!!!!!!!!!!!
치위생학과 있음!!!!!!!!!!!!
정

In [11]:
temp = list(new_job['내용'])

vectorizer = TfidfVectorizer()
text_list_vec = vectorizer.fit(temp)
word_index=text_list_vec.vocabulary_
text_list_vec=text_list_vec.transform(temp).toarray()
word_index = {v: k for k, v in word_index.items()}
word_index = sorted(word_index.items(), key=operator.itemgetter(0))


temp_jobkeyword = []
for j in range(len(new_job)):

    index_of_major = j 
    

    result={}
    for i in range(len(text_list_vec[index_of_major])):
        if text_list_vec[index_of_major][i] != 0:
            result[word_index[i][1]] =  text_list_vec[index_of_major][i]
    result= sorted(result.items(), key=operator.itemgetter(1),reverse=True)
    top50=[]
    for x in range(50):
        top50.append(result[x][0])


    temp_jobkeyword.append(top50)
    
    
    
    
cleaned_job = cleaned_job.assign(키워드 = temp_jobkeyword)
cleaned_job

직업                   학과  \
0    플로리스트              원예학과                  
1    화학자                화학과                   
2    항공교통관제사            교통공학과                 
3    방송작가               문예창작학과                
4    유치원교사              유아교육학과                
5    생물학연구원             생물학과                  
6    가상현실전문가            소프트웨어공학과              
7    음악(미술)교사           음악(미술)교육학과            
8    목사                 종교학과                  
9    직업상담사              교육학과                  
10   GIS전문가             지질학과                  
11   국문학자               국어국문학과                
12   빅데이터전문가            통계학과                  
13   수학교사               수학교육학과                
14   사서                 문헌정보학과                
15   기상연구원              지구과학과                 
16   과학교사               과학교육학과                
17   초등교사               초등교육학과                
18   사회(지리, 역사, 윤리)교사   사회(지리, 역사, 윤리)교육학과    
19   해양수산기술자            수산학과                  
20   체육교사               체육교육학과                
21   언어학연구원             언어학과                  
22   (공학)전문교과교사         공학교육학과                
23   기후변화전문가            대기과학과                 
24   투자분석가              경제학과                  
25   법무사                법학과                   
26   호텔컨시어지             호텔경영학과                
27   토목공학기술자            토목공학과                 
28   물류관리사              무역학과                  
29   회계사                회계학과                  
30   광고홍보전문가            광고홍보학과                
31   보육교사               아동학과                  
32   전기공학기술자            전기공학과                 
33   공무원                행정학과                  
34   사회복지사              사회복지학과                
35   헤드헌터               사회학과                  
36   응용소프트웨어개발자         응용소프트웨어공학과            
37   기자                 정치외교학과                
38   경찰관                경찰행정학과                
39   사물인터넷개발자           반도체공학과                
40   국제회의전문가            국제관계학과                
41   위생사                보건학과                  
42   웹디자이너              시각디자인학과               
43   CF감독               영상예술학과                
44   군인                 군사학과                  
45   보험계리사              금융보험학과                
46   식품공학자              식품가공학과                
47   생명공학연구원            생명과학과                 
48   수의사                수의학과                  
49   공항검역관              동물자원학과                
50   푸드스타일리스트           식품조리학과                
51   환경컨설턴트(사회)         도시계획학과                
52   환경컨설턴트(자연)         환경학과                  
53   공예원                공예학과                  
54   패션디자이너             의류학과                  
55   수학자                수학과                   
56   안무가                무용학과                  
57   피부관리사              미용과                   
58   물리학자               물리학과                  
59   스포츠트레이너            체육학과                  
60   건축공학기술자            건축공학과                 
61   원예기술자              식물자원학과                
62   항공우주공학기술자          항공우주공학과               
63   도시계획가              도시공학과                 
64   해양공학기술자            해양공학과                 
65   로봇공학기술자            제어로봇공학과               
66   기계공학기술자            기계공학과                 
67   웹툰작가               만화애니메이션학과             
68   금속공학기술자            금속공학과                 
69   자동차공학기술자           자동차공학과                
70   치과기공사              치기공학과                 
71   한약사                한약과                   
72   에너지공학기술자           에너지공학과                
73   전자공학기술자            전자공학과                 
74   섬유공학기술자            섬유공학과                 
75   재료공학기술자            신소재공학과                
76   디지털포렌식수사관          컴퓨터공학과                
77   치과의사               치의예과                  
78   게임프로그래머            정보통신공학과               
79   의사                 의예과                   
80   약사                 약학과                   
81   한의사                한의예과                  
82   간호사                간호학과                  
83   응급구조사              응급구조학과                
84   임상병리사              임

In [12]:
temp = list(new_major['내용'])

vectorizer = TfidfVectorizer()
text_list_vec = vectorizer.fit(temp)
word_index=text_list_vec.vocabulary_
text_list_vec=text_list_vec.transform(temp).toarray()
word_index = {v: k for k, v in word_index.items()}
word_index = sorted(word_index.items(), key=operator.itemgetter(0))


temp_majorkeyword = []
for j in range(len(new_major)):

    index = j 
    

    result={}
    for i in range(len(text_list_vec[index])):
        if text_list_vec[index][i] != 0:
            result[word_index[i][1]] =  text_list_vec[index][i]
    result= sorted(result.items(), key=operator.itemgetter(1),reverse=True)
    top30=[]
    
    for x in range(30):
        top30.append(result[x][0])


    temp_majorkeyword.append(top30)
    
    
    
    
cleaned_major = cleaned_major.assign(키워드 = temp_majorkeyword)
cleaned_major

학과  \
0    경영정보학과          
1    노어노문학과          
2    동양어문학과          
3    문예창작학과          
4    문헌정보학과          
5    (고고)문화인류학과      
6    문화재학과           
7    북한학과            
8    불어불문학과          
9    사학과             
10   관현악과            
11   스페인어학과          
12   심리학과            
13   언어학과            
14   영어통번역학부         
15   일어일문학과          
16   국제학부            
17   자율전공학부          
18   경영학과            
19   공공행정학과          
20   관광경영학과          
21   공공인재학과          
22   글로벌경영학과         
23   관광학과            
24   광고홍보학과          
25   국제관계학과          
26   군사학과            
27   금융보험학과          
28   기술경영학과          
29   농업경제학과          
30   도시계획부동산학과       
31   도시행정학과          
32   무역학과            
33   미디어학부           
34   수학교육과           
35   아동복지학과          
36   부동산학과           
37   사회복지학과          
38   세무회계학과          
39   언론정보학과          
40   식품자원경제학과        
41   신문방송학과          
42   아동-청소년학과        
43   응용통계학과          
44   의료경영학과          
45   치위생학과           
46   정치외교학과          
47   지리학과            
48   행정학과            
49   항공서비스학과         
50   호텔경영학과          
51   과학교육과           
52   교육공학과           
53   방사선학과           
54   국어교육과           
55   물리교육과           
56   미술교육과           
57   영어교육과           
58   생물교육과           
59   임산생명공학과         
60   역사교육과           
61   윤리교육과           
62   일반사회교육과         
63   일어교육과           
64   줄기세포재생공학과       
65   지리교육과           
66   초등교육과           
67   한문교육과           
68   환경교육과           
69   공업화학과           
70   가정아동복지학과        
71   대기환경과학과         
72   농생물학과           
73   대기과학과           
74   멀티미디어학과         
75   미래농업융합학부        
76   미생물분자생명과학과      
77   모바일공학과          
78   분자생물학과          
79   산림학과            
80   산림환경시스템학과       
81   생물환경화학과         
82   수학과             
83   천문우주학과          
84   식물자원학과          
85   식품영양학과          
86   건설시스템공학과        
87   정보통계학과          
88   외식산업학과          
89   응용물리학과          
90   응용수학과           
91   의류학과            
92   산업공학과           
93   지구시스템과학과        
94   지질환경과학과         
95   해양학과            
96   화학과             
97   스포츠산업학과         
98   환경학과            
99   게임공학과           
100  고분자공학과          
101  공간정보공학과         
102  교통공학과           
103  생물공학과           
104  드론교통공학과         
105  반도체공학과          
106  도시공학과           
107  디지털콘텐츠학과        
108  멀티미디어공학과        
109  메카트로닉스공학과       
110  반도체시스템공학과       
111  산업경영공학과         
112  산업시스템공학과        
113  생명공학과           
114  세라믹공학과          
115  소프트웨어융합공학과      
116  신소재공학과          
117  에너지공학과          
118  자동차IT융합학과       
119  전자공학과           
120  식품공학과           
121  재료공학과           
122  정보보안학과          
123  정보보호학과          
124  조선해양공학과         
125  조선해양시스템공학과      
126  지역건설공학과         
127  토목공학과           
128  항공우주공학과         
129  컴퓨터공학과          
130  해양공학과           
131  항해학부            
132  화장품공학과          
133  간호학과            
134  건강관리학과          
135  물리치료학과          
136  산업보건학과          
137  수의예과            
138  안경광학과           
139  응급구조학과          
140  약학과             
141  언어청각치료학과        
142  의예과             
143  재활학과            
144  작업치료학과          
145  의공학과            
146  의료공학과           
147  의용생체공학과         
148  임상병리학과          
149  한약학과            
150  모델과             
151  뮤지컬학과           
152  치의예과            
153  경호학과            
154  스포츠과학과          
155  미술학과            
156  공업디자인학과         
157  유전공학과           
158  뷰티_미용_산업_예술학과   
159  무용학과            
160  유전공학과           
161  사회체육학과          
162  산업디자인학과         
163  서양화과            
164  성악과             
165  스포츠의학과_예체능      
166  영상디자인학과         
167  시각디자인학과         
168  환경디자인과          
169  연극영화학과          
170  조소과             
171  체육학과            
172  소비자학과           
173  패션디자인학과         
174  고고학과            
175  통계학과            
176  국어국문학과          
177  독어독문학과          
178  식품공학과           
179  문화콘텐츠학과         
180  신학과             
181  미술사학과  

In [13]:
relation_index=[]
relation_job=[]
for i in range(len(cleaned_major)):
    major = cleaned_major['학과'][i] 
    temp1=[]
    temp2=[]
    for j in range(len(cleaned_job)):
        if (major in cleaned_job['학과'][j]) or (major in cleaned_job['관련학과'][j]):
            temp1.append(cleaned_job['직업'][j])
            temp2.append(j)
    relation_job.append(temp1)
    relation_index.append(temp2)

cleaned_major = cleaned_major.assign(relation_job = relation_job)    
cleaned_major = cleaned_major.assign(relation_job_index = relation_index)

In [14]:
cleaned_major

학과  \
0    경영정보학과          
1    노어노문학과          
2    동양어문학과          
3    문예창작학과          
4    문헌정보학과          
5    (고고)문화인류학과      
6    문화재학과           
7    북한학과            
8    불어불문학과          
9    사학과             
10   관현악과            
11   스페인어학과          
12   심리학과            
13   언어학과            
14   영어통번역학부         
15   일어일문학과          
16   국제학부            
17   자율전공학부          
18   경영학과            
19   공공행정학과          
20   관광경영학과          
21   공공인재학과          
22   글로벌경영학과         
23   관광학과            
24   광고홍보학과          
25   국제관계학과          
26   군사학과            
27   금융보험학과          
28   기술경영학과          
29   농업경제학과          
30   도시계획부동산학과       
31   도시행정학과          
32   무역학과            
33   미디어학부           
34   수학교육과           
35   아동복지학과          
36   부동산학과           
37   사회복지학과          
38   세무회계학과          
39   언론정보학과          
40   식품자원경제학과        
41   신문방송학과          
42   아동-청소년학과        
43   응용통계학과          
44   의료경영학과          
45   치위생학과           
46   정치외교학과          
47   지리학과            
48   행정학과            
49   항공서비스학과         
50   호텔경영학과          
51   과학교육과           
52   교육공학과           
53   방사선학과           
54   국어교육과           
55   물리교육과           
56   미술교육과           
57   영어교육과           
58   생물교육과           
59   임산생명공학과         
60   역사교육과           
61   윤리교육과           
62   일반사회교육과         
63   일어교육과           
64   줄기세포재생공학과       
65   지리교육과           
66   초등교육과           
67   한문교육과           
68   환경교육과           
69   공업화학과           
70   가정아동복지학과        
71   대기환경과학과         
72   농생물학과           
73   대기과학과           
74   멀티미디어학과         
75   미래농업융합학부        
76   미생물분자생명과학과      
77   모바일공학과          
78   분자생물학과          
79   산림학과            
80   산림환경시스템학과       
81   생물환경화학과         
82   수학과             
83   천문우주학과          
84   식물자원학과          
85   식품영양학과          
86   건설시스템공학과        
87   정보통계학과          
88   외식산업학과          
89   응용물리학과          
90   응용수학과           
91   의류학과            
92   산업공학과           
93   지구시스템과학과        
94   지질환경과학과         
95   해양학과            
96   화학과             
97   스포츠산업학과         
98   환경학과            
99   게임공학과           
100  고분자공학과          
101  공간정보공학과         
102  교통공학과           
103  생물공학과           
104  드론교통공학과         
105  반도체공학과          
106  도시공학과           
107  디지털콘텐츠학과        
108  멀티미디어공학과        
109  메카트로닉스공학과       
110  반도체시스템공학과       
111  산업경영공학과         
112  산업시스템공학과        
113  생명공학과           
114  세라믹공학과          
115  소프트웨어융합공학과      
116  신소재공학과          
117  에너지공학과          
118  자동차IT융합학과       
119  전자공학과           
120  식품공학과           
121  재료공학과           
122  정보보안학과          
123  정보보호학과          
124  조선해양공학과         
125  조선해양시스템공학과      
126  지역건설공학과         
127  토목공학과           
128  항공우주공학과         
129  컴퓨터공학과          
130  해양공학과           
131  항해학부            
132  화장품공학과          
133  간호학과            
134  건강관리학과          
135  물리치료학과          
136  산업보건학과          
137  수의예과            
138  안경광학과           
139  응급구조학과          
140  약학과             
141  언어청각치료학과        
142  의예과             
143  재활학과            
144  작업치료학과          
145  의공학과            
146  의료공학과           
147  의용생체공학과         
148  임상병리학과          
149  한약학과            
150  모델과             
151  뮤지컬학과           
152  치의예과            
153  경호학과            
154  스포츠과학과          
155  미술학과            
156  공업디자인학과         
157  유전공학과           
158  뷰티_미용_산업_예술학과   
159  무용학과            
160  유전공학과           
161  사회체육학과          
162  산업디자인학과         
163  서양화과            
164  성악과             
165  스포츠의학과_예체능      
166  영상디자인학과         
167  시각디자인학과         
168  환경디자인과          
169  연극영화학과          
170  조소과             
171  체육학과            
172  소비자학과           
173  패션디자인학과         
174  고고학과            
175  통계학과            
176  국어국문학과          
177  독어독문학과          
178  식품공학과           
179  문화콘텐츠학과         
180  신학과             
181  미술사학과  

In [15]:
cleaned_major.to_csv('cleaned_major.csv')
cleaned_job.to_csv('cleaned_job.csv')